In [2]:
from cs1lib import *
from math import sqrt

WINDOW_WIDTH = 400
WINDOW_HEIGHT = 400

FRAME_RATE = 60 
TIMESTEP = .5 / FRAME_RATE

PIXELS_PER_METER = 10.0

INITIAL_X = 22.0
INITIAL_Y = 25.0
INITIAL_V_X = 0.1
INITIAL_V_Y = 0.5

BALL_RADIUS = 10

CLIMBER_MASS = 20
BELAYER_MASS = 30
SPRING_CONSTANT = 500.0   
G = -9.8


DAMPING_FACTOR = 1.0
METERS_OF_SLACK = 5

POST_X = 20.0
POST_Y = 20.0
POST_RADIUS = 5     

# Climber position
x = INITIAL_X
y = INITIAL_Y

# Climber velocity
v_x = INITIAL_V_X
v_y = INITIAL_V_Y

# Belay position and velocity

x_belayer = 20
y_belayer = 2
v_x_belayer = 0
v_y_belayer = 0

In [3]:

def draw_body(x, y, filename):
    disable_stroke()
    x_pixels = x * PIXELS_PER_METER
    y_pixels = WINDOW_HEIGHT - y * PIXELS_PER_METER

    body = load_image(filename)
    draw_image(body, x_pixels, y_pixels, 15, 15)
    

def draw_rope(x, y):
    enable_stroke()
    set_stroke_width(2)
    set_stroke_color(0, 0, 0)

    x_pixels = x * PIXELS_PER_METER
    y_pixels = WINDOW_HEIGHT - y * PIXELS_PER_METER
    px_pixels = POST_X * PIXELS_PER_METER
    py_pixels = WINDOW_HEIGHT - POST_Y * PIXELS_PER_METER

    draw_line(px_pixels, py_pixels, x_pixels, y_pixels)

    # Draw the post.
    disable_stroke()
    set_fill_color(0.6, 0, 0)
    for i in range(5): 
        draw_circle(px_pixels, py_pixels  + i * 30, POST_RADIUS)

    

def compute_next_position(position, velocity, timestep):
    return position + velocity * timestep

def compute_next_velocity(velocity, acceleration, timestep, damping=True):
    global DAMPING_FACTOR
    if y < 20 and damping:      
        DAMPING_FACTOR *=1.0002
    if y <=1: #if hitting the ground
        return 0
    return velocity/DAMPING_FACTOR + acceleration * timestep
    

def distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return sqrt(dx * dx + dy * dy)

def compute_spring_force(x1, y1, x2, y2, k):
    
    #the rope exerts no force until all the slack is pulled through 
    if y > POST_X - METERS_OF_SLACK:
        return 0
    
    return distance(x1, y1, x2, y2) * k

In [4]:
def main():
    global x, y, v_x, v_y, x_belayer, y_belayer, v_x_belayer, v_y_belayer

    set_clear_color(1, 1, 1)

    # Draw the current frame.
    clear()
    background = load_image("bg.jpg")
    draw_image(background, 0, 0)
    
    #climber and climber's end of rope

    draw_body(x, y, "climber.png")
    draw_rope(x, y)    
    
    #belayer and belayer's end of rope
    draw_body(x_belayer, y_belayer, "climber.png")
    draw_rope(x_belayer, y_belayer)
 

    draw_line(20, 8, 20, 4) #middle section of rope
    
    

    x = compute_next_position(x, v_x, TIMESTEP)
    y = compute_next_position(y, v_y, TIMESTEP)

    # Compute the current magnitude of acceleration of the ball.
    f = compute_spring_force(POST_X, POST_Y, x, y, SPRING_CONSTANT)

    a = f / CLIMBER_MASS
    

    # Compute a_x and a_y, the x and y components of the acceleration.
    d = distance(POST_X, POST_Y, x, y)
    dir_x = (POST_X - x) / d
    dir_y = (POST_Y - y) / d
    a_x = dir_x * a
    a_y = dir_y * a + G

    # Given the current accelerations, compute next velocities.
    v_x = compute_next_velocity(v_x, a_x, TIMESTEP, damping=False)
    v_y = compute_next_velocity(v_y, a_y, TIMESTEP)
    
    #for the belayer, who is directy below the rope and only moves up.
    #the factor of 0.8 represents the reduced acceleration due to friction 
    #of the rope running through the entire system
    a_y_belayer = (f / BELAYER_MASS) * .8 

    y_belayer = compute_next_position(y_belayer, v_y_belayer, TIMESTEP)
    v_y_belayer = compute_next_velocity(v_y_belayer, a_y_belayer, TIMESTEP)
    

start_graphics(main, 600, framerate=FRAME_RATE)

SystemExit: 0

C:\Users\CLK\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3275: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
